# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np
import os
import s3fs
import re
import warnings

Configuration de l'accès aux données

In [2]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

In [3]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})


# Import cleaning and merge functions

exec(open('0_Cleaning_and_merge_functions.py').read())

exec(open('0_KPI_functions.py').read())

# Ignore warning
warnings.filterwarnings('ignore')


In [4]:
def load_dataset_2(directory_path, file_name):
    """
    This function loads csv file
    """
    file_path = "bdc2324-data" + "/" + directory_path + "/" + directory_path + file_name + ".csv"
    with fs.open(file_path, mode="rb") as file_in:
        df = pd.read_csv(file_in, sep=",")

    # drop na :
    #df = df.dropna(axis=1, thresh=len(df))
    # if identifier in table : delete it
    if 'identifier' in df.columns:
        df = df.drop(columns = 'identifier')
    return df

In [5]:
def export_in_temporary(df, output_name):
    print('Export of dataset :', output_name)
    FILE_PATH_OUT_S3 = "projet-bdc2324-team1/Temporary" + "/" + output_name + '.csv'
    with fs.open(FILE_PATH_OUT_S3, 'w') as file_out:
        df.to_csv(file_out, index = False)

# Cleaning target area and tags

In [ ]:
target_example = preprocessing_target_area('1')

In [6]:
tenant_id = '1'

def concatenate_names(names):
    return ', '.join(names)
    
target_example =display_input_databases(tenant_id, "target_information")

target_example['target_name'] = target_example['target_name'].fillna('').str.lower()


target_example['target_jeune'] = target_example['target_name'].str.contains('|'.join(['jeune', 'pass_culture', 'etudiant', '12-25 ans', 'student', 'jeunesse']), case=False).astype(int)
target_example['target_optin'] = target_example['target_name'].str.contains('|'.join(['optin' ,'opt-in']), case=False).astype(int)
target_example['target_optout'] = target_example['target_name'].str.contains('|'.join(['optout', 'unsubscribed']), case=False).astype(int)
target_example['target_scolaire'] = target_example['target_name'].str.contains('|'.join(['scolaire' , 'enseignant', 'chercheur', 'schulen', 'école']), case=False).astype(int)
target_example['target_entreprise'] = target_example['target_name'].str.contains('|'.join(['b2b', 'btob', 'cse']), case=False).astype(int)
target_example['target_famille'] = target_example['target_name'].str.contains('|'.join(['famille', 'enfants', 'family']), case=False).astype(int)
target_example['target_newsletter'] = target_example['target_name'].str.contains('|'.join(['nl', 'newsletter']), case=False).astype(int)



target_agg = target_example.groupby('customer_id').agg(
    nb_targets=('target_name', 'nunique'),  # Utilisation de tuples pour spécifier les noms de colonnes
    all_targets=('target_name', concatenate_names),
    all_target_types=('target_type_name', concatenate_names)
    ).reset_index()

target_example_categorie = target_example.groupby('customer_id')[['target_jeune', 'target_optin', 'target_optout', 'target_scolaire', 'target_entreprise', 'target_famille', 'target_newsletter']].max()

target_example_categorie.head()

File path :  projet-bdc2324-team1/0_Input/Company_1/target_information.csv


target_jeune  target_optin  target_optout  target_scolaire  \
customer_id                                                               
1                       1             1              1                1   
2                       1             1              1                1   
3                       1             1              0                0   
4                       1             1              0                0   
5                       1             1              0                0   

             target_entreprise  target_famille  target_newsletter  
customer_id                                                        
1                            1               0                  0  
2                            1               0                  1  
3                            0               0                  1  
4                            0               0                  0  
5                            0               0                  0

In [ ]:
#export_in_temporary(target_agg, 'Target_kpi_concatenate')

# Brouillon

In [ ]:

def display_covering_time(df, company, datecover):
    """
    This function draws the time coverage of each company
    """
    min_date = df['purchase_date'].min().strftime("%Y-%m-%d")
    max_date = df['purchase_date'].max().strftime("%Y-%m-%d")
    datecover[company] = [datetime.strptime(min_date, "%Y-%m-%d") + timedelta(days=x) for x in range((datetime.strptime(max_date, "%Y-%m-%d") - datetime.strptime(min_date, "%Y-%m-%d")).days)]
    print(f'Couverture Company {company} : {min_date} - {max_date}')
    return datecover


def compute_time_intersection(datecover):
    """
    This function returns the time coverage for all companies
    """
    timestamps_sets = [set(timestamps) for timestamps in datecover.values()]
    intersection = set.intersection(*timestamps_sets)
    intersection_list = list(intersection)
    formated_dates = [dt.strftime("%Y-%m-%d") for dt in intersection_list]
    return sorted(formated_dates)


def df_coverage_modelization(sport, coverage_features = 0.7):
    """
    This function returns start_date, end_of_features and final dates
    that help to construct train and test datasets
    """
    datecover = {}
    for company in sport:
        df_products_purchased_reduced = display_input_databases(company, file_name = "products_purchased_reduced",
                                                          datetime_col = ['purchase_date'])
        datecover = display_covering_time(df_products_purchased_reduced, company, datecover)
    #print(datecover.keys())
    dt_coverage = compute_time_intersection(datecover)
    start_date = dt_coverage[0]
    end_of_features = dt_coverage[int(0.7 * len(dt_coverage))]
    final_date = dt_coverage[-1]
    return start_date, end_of_features, final_date
 

# Bases non communes : mise à plat

In [ ]:
companies = {'musee' : ['1', '2', '3', '4'],
            'sport': ['5', '6', '7', '8', '9'],
            'musique' : ['10', '11', '12', '13', '14']}

all_companies = ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14']

In [ ]:
companies_databases = pd.DataFrame()

for i in all_companies:
    company_databases = pd.DataFrame({'company_number' : [i]})

    BUCKET = "bdc2324-data/"+i
    for base in fs.ls(BUCKET):
        match = re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', base)
        if match:
            nom_base = match.group(3)
            company_databases[nom_base] = 1

    companies_databases = pd.concat([companies_databases, company_databases])

In [ ]:
pd.set_option("display.max_columns", None)
companies_databases


In [ ]:
pd.reset_option("display.max_columns")

# Debut Travail 25/02

## Base communes au types Musée

In [ ]:
companies['musee']

In [ ]:
for i in companies['musique']:
    BUCKET = "bdc2324-data/"+i
    liste_base = []
    for base in fs.ls(BUCKET):
        match = re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', base)
        if match:
            nom_base = match.group(3)
            liste_base.append(nom_base)
    globals()['base_'+i] = liste_base


In [ ]:
# Trouver l'intersection entre les cinq listes
intersection = set(base_1).intersection(base_2, base_3, base_4, base_101)

# Convertir le résultat en liste si nécessaire
intersection_liste = list(intersection)

print(intersection_liste)

In [ ]:
# Trouver l'intersection entre les cinq listes
intersection = set(base_10).intersection(base_12, base_13, base_14, base_11)

# Convertir le résultat en liste si nécessaire
intersection_liste = list(intersection)

print(intersection_liste)

In [ ]:
len(intersection_liste)

In [ ]:
df1_tags = load_dataset_2("1", "tags")

In [ ]:
df1_structure_tag_mappings = load_dataset_2("1", 'structure_tag_mappings')

In [ ]:
df1_customersplus = load_dataset_2("1", "customersplus")

In [ ]:
df1_customersplus.groupby('structure_id')['id'].count().reset_index().sort_values('id', ascending=False).head(20)

In [ ]:
df1_customersplus['structure_id'].isna().sum() / len(df1_customersplus['structure_id'])

In [ ]:
len(df1_structure_tag_mappings)

In [ ]:
df1_structure_tag_mappings.groupby('tag_id')['structure_id'].count().reset_index().sort_values('structure_id', ascending=False).head(20)

In [ ]:
?np.sort_values()

In [ ]:
def info_colonnes_dataframe(df):
    # Créer une liste pour stocker les informations sur chaque colonne
    infos_colonnes = []

    # Parcourir les colonnes du DataFrame
    for nom_colonne, serie in df.items():  # Utiliser items() au lieu de iteritems()
        # Calculer le taux de valeurs manquantes
        taux_na = serie.isna().mean() * 100

        # Ajouter les informations à la liste
        infos_colonnes.append({
            'Nom_colonne': nom_colonne,
            'Type_colonne': str(serie.dtype),
            'Taux_NA': taux_na
        })

    # Créer une nouvelle DataFrame à partir de la liste d'informations
    df_infos_colonnes = pd.DataFrame(infos_colonnes)

    return df_infos_colonnes

In [ ]:
info_colonnes_dataframe(df1_tags)

In [ ]:
info_colonnes_dataframe(df1_structure_tag_mappings)

In [ ]:
pd.set_option('display.max_colwidth', None)

print(df1_tags['name'])

In [ ]:
pd.set_option('display.max_rows', None)

In [ ]:
print(df1_tags['name'])

## KPI sur target_type

In [7]:
pd.set_option('display.max_colwidth', None)


Raisonnement : on prends les target_type qui représente 90% des clients et on fait des catégories dessus.

In [8]:
def print_main_target(tenant_id, nb_print = 40):
    df_target = display_input_databases(tenant_id, "target_information")

    print('Nombre de ciblage : ', len(df_target))
    nb_customers = df_target['customer_id'].nunique()
    print('Nombre de client avec étiquette target : ', nb_customers) 

    nb_custumers_per_target = df_target.groupby("target_name")['customer_id'].count().reset_index().sort_values('customer_id', ascending=False)
    nb_custumers_per_target['cumulative_customers'] = nb_custumers_per_target['customer_id'].cumsum()/len(df_target)
    nb_custumers_per_target['customer_id'] = nb_custumers_per_target['customer_id']/nb_customers

    return nb_custumers_per_target.head(nb_print)

In [ ]:
pd.set_option('display.max_rows', None)

In [9]:
pd.set_option("max_colwidth", None)
print_main_target('1', 60)

File path :  projet-bdc2324-team1/0_Input/Company_1/target_information.csv
Nombre de ciblage :  768024
Nombre de client avec étiquette target :  151159


target_name  \
161                        consentement optin mediation specialisee   
160                                 consentement optin jeune public   
158                                          consentement optin b2c   
5                                  Arenametrix_bascule tel vers sib   
165                                         consentement optout b2c   
19                            COM Inscrits NL générale (historique)   
162                          consentement optin newsletter generale   
169                         consentement optout newsletter generale   
170                                   consentement optout scolaires   
166                                         consentement optout dre   
164                                         consentement optout b2b   
126     Inscrits NL générale (export_291019 + operation_videomaton)   
157                                          consentement optin b2b   
216                                       ddcp_visiteurs dps 010622   
20                                          Contacts_prenomsdoubles   
115                           FORMATION _ acheteurs optin last year   
214                   ddcp_promo_visiteurs occasionnels_musee_8mois   
189                                  ddcp_promo_md_musée_dps 011019   
188                    ddcp_promo_MD_billet_musée_oct_2019_agarder2   
163                                    consentement optin scolaires   
159                                          consentement optin dre   
34                                      DDCP Newsletter enseignants   
36                                     DDCP Newsletter jeune public   
127                                   Inscrits NL générale site web   
145                                            Votre première liste   
61                                             DDCP billets famille   
106                                                    DRE MucemLab   
39                              DDCP Newsletter relais champ social   
110                                             DRE institutionnels   
48            DDCP PROMO Participants ateliers (adultes et enfants)   
74                                DDCP promo Plan B 2019 (concerts)   
72                           DDCP promo MD pass musées dps oct 2018   
94                                     DDCP rentrée culturelle 2023   
23                                         DDCP MD Procès du Siècle   
186                                 ddcp_md_scene_ouverte_au_talent   
108                                                  DRE chercheurs   
220                                             festival_jean_rouch   
105                                         DRE Festival Jean Rouch   
275                               structures_etiquette champ social   
86   DDCP promo spectateurs prog 21-22 (spectacles, ciné, ateliers)   
128                               Inscrits NL jeune public site web   
260                                               rappel po barvalo   
104                                        DDCP_marseille_jazz_2023   
32                               DDCP Newsletter centres de loisirs   
13                                        Autres_interet_exposition   
228                    import_arenametrix_contactstousecardouv_expo   
117                                       Formation clients fidèles   
22                                                   DDCP Cine 2023   
40                                                  DDCP OLBJ! 2023   
240                           journee-de-l-inclusion_20230601_21h25   
137                          Questionnaire 2 satisfaction scolaire    
93                     DDCP rendez-vous de septembre offre spéciale   
135                                           Plan B 2018 (électro)   
270                                         save_the_date_populaire   
132                                     Newsletter CCR (passerelle)   
116      Fichier institutionnel (ne pas utiliser sans autorisation)   
222      

In [11]:
pd.set_option('display.max_rows', None)


In [ ]:
pd.reset_option('display.max_rows')

In [ ]:
print_main_target('2', 25)

In [ ]:
print_main_target('3', 70)

In [ ]:
print_main_target('4', 100)

In [ ]:
pd.set_option('display.max_rows', None)

print_main_target('5', 100)

In [ ]:
print_main_target('6', 100)

In [ ]:
print_main_target('7', 100)

In [ ]:
print_main_target('8', 100)

In [12]:
print_main_target('9', 100)

File path :  projet-bdc2324-team1/0_Input/Company_9/target_information.csv
Nombre de ciblage :  1399179
Nombre de client avec étiquette target :  181136


target_name  \
184                                                                         Run Mate   
233                                                                        Triathlon   
77                                                                               HGM   
24                                                                       20km Genève   
75                                                                              GM23   
68                                                   GGM - inscrits 2015 - 2023 - FR   
85                                                     HGM - Inscrits 2005-2019 - FR   
187                                             RunMate - 500km autour montreux - FR   
188                                          RunMate - 500km autour montreux - FR v2   
46                                                          BDD - Semi & Marathon_FR   
83                                                              HGM - GM Public - FR   
84                                                    HGM - Inscrits 2005-2019 - ENG   
67                                                  GGM - inscrits 2015 - 2023 - ENG   
73                                                             GGM23 - inscrits - FR   
45                                                         BDD - Semi & Marathon_ENG   
82                                                             HGM - GM Public - ENG   
95                                                    LTGT - Inscrits 2008-2019 - FR   
186                                            RunMate - 500km autour montreux - ENG   
210                                                                     TMB - Opt-in   
118                                                                LTGT23-Amateur-FR   
88                                                               HGM désinscriptions   
213                                  TMB - anciens participants 2015 - 2020 - FR+ENG   
19                                                    20km - Inscrits 2017-2019 - FR   
100                                                 LTGT - inscrits 2015 - 2020 - FR   
10                                                        20KM23_Inscrit NL 25.10_FR   
185                                                         Run Mate désinscriptions   
303                                                                     test listes    
72                                                            GGM23 - inscrits - ENG   
9                                                                20KM23_FINISHER_FR2   
8                                                                 20KM23_FINISHER_FR   
38                                                             20km23_nl finisher fr   
107                                                         LTGT21 - Inscrits FR+ENG   
33                                                     20km23_inscrits fr 05.10_test   
25                                                       20km Genève désinscriptions   
113                                                          LTGT22 - inscris FR+ENG   
47                                                             Bénévoles Mass Events   
32                                                          20km23_inscrits fr 02.10   
64                                                               GGM - Contact PT OK   
112  LTGT22 - Anciens participants Half, Half relais, standard, standard relais - FR   
225                                                                 TMB23-Amateur-FR   
110                                                             LTGT21 - inscrits FR   
219                                                              TMB22 - inscrits FR   
94                                                   LTGT - Inscrits 2008-2019 - ENG   
115                                                             LTGT22 - inscrits FR   
203                                                          TIMB22 - incritS FR+ENG   
29                       

In [13]:
print_main_target('10', 100)

File path :  projet-bdc2324-team1/0_Input/Company_10/target_information.csv
Nombre de ciblage :  69258
Nombre de client avec étiquette target :  53639


target_name  customer_id  \
9                             Newsletter mensuelle     0.722068   
2                                       Blackliste     0.188669   
36                     import opt-in février 2023     0.068141   
37                          import opt-out fév 23     0.055016   
5                        Contacts opt-out 20.10.22     0.047726   
21                                 Théâtre amateur     0.033054   
41                           liste théâtre amateur     0.026641   
4                            CP EUH 7 octobre 2022     0.026492   
47                    spec Falaise - relance Mazut     0.020452   
35                 fichierspectateurs_recreatrales     0.016052   
29                   fichier news quartier grand t     0.007644   
33                  fichier2 news quartier grand t     0.007383   
23                   contacts amateurs 22-23 ok ok     0.006842   
22                  amateurs incandescences oct 22     0.006730   
25                      fichier invit Soir de fête     0.005984   
19                  Spectateurs Ce qu'il faut dire     0.004959   
49                               spec Mazut - tout     0.003300   
26  fichier invitation déjeuner chantier le 8 juin     0.003151   
0              3 M - spec du dimanche (toutes rep)     0.003132   
30              fichier op les dodos 21 nov global     0.003020   
8               Invitation protocolaire Les Fauves     0.002573   
1                3 M - spec du samedi (toutes rep)     0.002554   
28                       fichier jumelage halveque     0.002498   
27     fichier invitations pro les enfants d'amazi     0.002256   
18                   Spectateurs Acte(s) et sueurs     0.002237   
13                                     Presse 2021     0.002200   
20                    Spectateurs-rices SpaceSongs     0.002069   
15                            Presse Tous Terriens     0.002069   
46        nouveaux acheteurs 23-24 - relance Mazut     0.002032   
16                         Presse communqiué agglo     0.001920   
14                                    Presse 22-23     0.001883   
31              fichier presse grand t 23-24export     0.001864   
3     Bottière - jumelage (contacts proches projet     0.001566   
11                                             P6S     0.001286   
43                     mails permanents gd t fev23     0.000932   
34    fichiercontactstous_enssup_relance étudiants     0.000820   
42                   mails intervenants mdla fev23     0.000522   
48                                    spec Jessica     0.000522   
7          Invit conf presse EUH : artistes + DRAC     0.000466   
10                                             P2S     0.000392   
39       liste intervenants mdla_newsletter temuda     0.000392   
12                            Personnel du Grand T     0.000354   
44                     mails permanents mdla fev23     0.000336   
32                  fichier-sante-social-terminato     0.000317   
40         liste permanents mdla_newsletter temuda     0.000317   
17                                Presse éducation     0.000131   
38                               liste billetterie     0.000056   
6                               Equipe com Grand T     0.000056   
45                   news jumelage Bottière ajouts     0.000056   
24                       emails yohann et tiphaine     0.000056   

    cumulative_customers  
9               0.559228  
2               0.705348  
36              0.758122  
37              0.800731  
5               0.837694  
21              0.863294  
41              0.883927  
4               0.904444  
47              0.920284  
35              0.932715  
29              0.938635  
33              0.944353  
23              0.949652  
22              0.954864  
25              0.959499  
19              0.963340  
49              0.965896  
26              0.968336  
0               0.970762  
30              0.973101  
8               0.975093  
1               0.977071  


In [14]:
print_main_target('11', 100)


File path :  projet-bdc2324-team1/0_Input/Company_11/target_information.csv
Nombre de ciblage :  124302
Nombre de client avec étiquette target :  62915


target_name  customer_id  \
50                          Temp - DOUBLE OPTIN     0.410983   
31                Nombre de représentations = 1     0.330128   
65             primo-spectateurs (fidélité = 1)     0.247811   
0           Acheteurs réguliers (fidélité >= 2)     0.126202   
34           Nombre de représentations = ou > 4     0.085290   
2                    Brochure janvier-juin 2023     0.076929   
30                                   NEWSLETTER     0.074370   
5                  Demande brochure sept-déc 23     0.071541   
6              Demande brochure sept-déc 23 DEF     0.071461   
32                Nombre de représentations = 2     0.071016   
52                              Waterproof_2023     0.065326   
46                      Relance Poppée 08/09/23     0.057077   
28                           Luisa Miller_ciblé     0.052404   
10                              En dernier lieu     0.036287   
1                            Bilan Carmen danse     0.030660   
33                Nombre de représentations = 3     0.029023   
18                       Inscription Newsletter     0.019026   
4                                Code postal 56     0.015481   
23        Les nuits d'été - mail ciblé 13/10/23     0.011825   
42                  Poppée 5, 7 et 8 octobre 23     0.008901   
43     Promo musique du monde Mawâl de la terre     0.008122   
38                             PRESSE NATIONALE     0.006978   
20                  L'Élixir d'amour 11, 13 mai     0.006390   
12                         Florilège mail ciblé     0.006390   
22            Les Nuits d'été - avant spectacle     0.006056   
11                         Enquête_Bal de Paris     0.005786   
27                         Luisa Miller 23 mars     0.004339   
24  Les nuits d'été ajout - mail ciblé 13/10/23     0.003465   
13                            GRANDS EVENEMENTS     0.003386   
41                          Poppée 3 octobre 23     0.002416   
62                    liste mécénat et prospect     0.002273   
40               Poppée 1 octobre 23 uniquement     0.002162   
21                 L'Élixir d'amour 5, 7, 9 mai     0.002098   
37                                PRESSE LOCALE     0.001891   
26                   Luisa Miller 23 et 25 mars     0.001764   
59                     liste invites grand boum     0.001637   
16                             INVITS PREMIERES     0.001494   
25                   Luisa Miller 19 et 21 mars     0.001446   
19                                  Invités TNB     0.001208   
44                        Protocole : REGIONAUX     0.001160   
54                                  assos danse     0.001160   
45                  Protocole Objectif Choeurs      0.001160   
51                      Titulaires cartes Opéra     0.000985   
7                    Ecoles élémentaires Rennes     0.000954   
53                       Zaïde 10 et 12 février     0.000827   
60        liste invités soirée 11 septembre mba     0.000795   
17                                 Info Tutelle     0.000795   
61      liste invités soirée 11 septembre mba 2     0.000763   
14                        Hira Gasy Spectateurs     0.000731   
48            Spectateurs Passion selon Brockes     0.000636   
47           Spectateurs Oratorios pour Passion     0.000525   
36                              PERSONNEL OPERA     0.000493   
57    invités représentation du 1er octobre2023     0.000445   
64                     mécène - vernissage frac     0.000429   
15                  INVITS CONF PRESSE ETE 2020     0.000381   
8                    Elixir d'amour 15/04 14h30     0.000350   
9                    Elixir d'amour 15/04 17h30     0.000350   
39                             PRESSE NUMERIQUE     0.000334   
55    invitations représentation 3 octobre2023     0.000334   
58            liste chargé.e.s de communication     0.000334   
29                                      MECENES     0.000207   
56       invités représentation 1er octobre2023     0.000207   
35  

In [15]:
print_main_target('12', 100)


File path :  projet-bdc2324-team1/0_Input/Company_12/target_information.csv
Nombre de ciblage :  1409140
Nombre de client avec étiquette target :  242726


target_name  customer_id  cumulative_customers
45                          CAT/buit all     0.755387              0.130116
274                    lista bbdd opt-in     0.510559              0.218061
157                          Obren mails     0.398466              0.286697
165        Participantes por primera vez     0.376012              0.351465
267                             buit all     0.355907              0.412771
158                      Obren mails CAT     0.302773              0.464924
94                                ES all     0.218934              0.502636
105            Festivals 19-21-22-23 CAT     0.213348              0.539385
51               Comptes cashless - tots     0.176883              0.569853
265            allcomptespersonalsambnom     0.176883              0.600321
264                  allcomptespersonals     0.176878              0.630789
268               compradores habituales     0.155327              0.657544
49                     Compradors CE2023     0.135478              0.680881
16                        All CE2023 CAT     0.116329              0.700918
160                       Obren mails ES     0.089224              0.716287
263            all unsubscribed 09.03.23     0.087766              0.731405
27             All unsubscribed 09.03.23     0.087766              0.746523
106             Festivals 19-21-22-23 ES     0.077594              0.759888
273                   lista bbdd opt out     0.076214              0.773016
171    Primer control de acceso 07/07/23     0.074710              0.785885
18                         All CE2023 ES     0.063673              0.796853
181          Push Joan Miquel Oliver CAT     0.056174              0.806529
200       Segments Joan Miquel Oliver AX     0.049978              0.815138
204                       Segments jajas     0.039996              0.822027
199           Segments Fatoumata PowerBI     0.037071              0.828412
278           segments fatoumata powerbi     0.037071              0.834798
88                      Divendres CE2023     0.036547              0.841093
205                   Segments jajas CAT     0.032349              0.846665
73                         Dijous CE2023     0.028448              0.851565
83                       Dissabte CE2023     0.028168              0.856417
201  Segments Joan Miquel Oliver PowerBI     0.027426              0.861142
279  segments joan miquel oliver powerbi     0.027426              0.865866
178                   Push Fatoumata CAT     0.027253              0.870560
93                                EN all     0.025675              0.874983
203       Segments Pinpilincinos PowerBI     0.020851              0.878574
280       segments pinpilincinos powerbi     0.020851              0.882166
78                       Dimecres CE2023     0.020702              0.885732
89                  Divendres CE2023 CAT     0.020463              0.889257
19                       All CE2023 buit     0.020002              0.892702
276                  regalentradesrondes     0.019458              0.896054
41         Assistents concerts last year     0.019458              0.899405
183               Push Pinpilincinos CAT     0.018708              0.902628
266               barres comedy festival     0.018066              0.905740
44                Barres Comedy festival     0.018066              0.908851
270                             in risus     0.018033              0.911958
50                   Compradors In Risus     0.018033              0.915064
182           Push Joan Miquel Oliver ES     0.017205              0.918027
22              All abo wkd-2dies CE2023     0.017097              0.920972
84                   Dissabte CE2023 CAT     0.016080              0.923742
42     Assistents concerts last year CAT     0.015878              0.926477
9                   Abonament Weekend ST     0.015400              0.929130
176                Push Al·lèrgiques CAT     0.014642              0.931652
7

In [17]:
print_main_target('14', 100)


File path :  projet-bdc2324-team1/0_Input/Company_14/target_information.csv
Nombre de ciblage :  779658
Nombre de client avec étiquette target :  240541


target_name  customer_id  \
11                                      BDS 17/18/19     0.371483   
28                   Cible non-acheteurs franciliens     0.208871   
34                          FHU 2018 - Acheteurs bds     0.184817   
14                                         BDS FHU18     0.184505   
12                                          BDS 2021     0.183229   
79                                     importer_huma     0.183229   
15                                         BDS FHU21     0.183224   
5                                      BCOM 17/18/19     0.162247   
16                                    BDS FHU23 VDéf     0.152298   
13                                          BDS 2022     0.139095   
29                   Cible non-acheteurs provinciaux     0.136991   
7                           BCOM 2023 - PASS 3 JOURS     0.106946   
55                           PROSPECT CONTACT -35ANS     0.103483   
73                              billets bds au 11/09     0.077604   
64                                           Pass 3J     0.070337   
9                                         BCOM FHU18     0.064214   
6                                          BCOM 2018     0.059470   
72                                  bds 2022 +50 ans     0.052519   
10                                        BCOM FHU19     0.045593   
36               Festivaliers WEB 2020 - plein tarif     0.045410   
19                                           CAMPING     0.041178   
41            Inscriptions newsletters (depuis 2019)     0.039598   
56                    PROSPECT FHU NORMANDIE 2021 #1     0.038925   
25                                     Camping FHU22     0.033716   
3                               ACTIVATION BDS 24/08     0.031862   
75                         data bcom 2023 - 15.06.23     0.026594   
20                                   CAMPING 2021 #1     0.022154   
21                                     CAMPING 24/08     0.022150   
58                    PROSPECT FHU NORMANDIE 2021 #3     0.020579   
54  PROSPECT ACHETEURS FHU23 POUR FHU NORMANDIE 2023     0.017901   
85      prospect acheteurs fhu23_pour_fhu rouen 2023     0.017901   
63                                PROSPECT NORMANDIE     0.014118   
60                   PROSPECT FHU NORMANDIE 2022 BDS     0.013777   
87                        prospect bds fhu normandie     0.013777   
44                                   PARKING 2021 #1     0.012484   
45                                     PARKING 24/08     0.012081   
42                                 PARKING - PORTE B     0.011848   
43                                 PARKING - PORTE J     0.011736   
86                       prospect bcom fhu normandie     0.010709   
59                  PROSPECT FHU NORMANDIE 2022 BCOM     0.010709   
50                                 PASS 3J - ENFANTS     0.009716   
49                                    PASS 3J - ADOS     0.008643   
18                                      BILLETS NUIT     0.007333   
51                        PASS Culture 2023 au 11/09     0.007092   
84                                pass culture 11/09     0.007092   
83                            pass culture - pass 3j     0.007076   
4                                         Ados FHU22     0.006718   
33                                     Enfants FHU22     0.006631   
46                                  PARKING CAMPEURS     0.004781   
39                       INSCRIPTION NL VOYAGES HUMA     0.003625   
17                                BILLET CAMPING-CAR     0.002594   
61                      PROSPECT FORUM LOGEMENT 2022     0.002062   
27                                 Camping-car FHU22     0.001996   
26                                 Camping Zen FHU22     0.001596   
66                        RESP. STANDS POUR FHUA2020     0.001559   
52                                       PRESSE 2021     0.001559   
70                       accreditations presse_fhu23     0.001434   
0                                ACCRED

## KPI sur tags

In [ ]:
customersplus = load_dataset_2("4", "customersplus")[['id', 'structure_id']]

In [ ]:
structure_tag_mappings = load_dataset_2('4', "structure_tag_mappings")[['structure_id', 'tag_id']]

In [ ]:
customersplus[customersplus['structure_id'].notna()]['structure_id'].nunique()

In [ ]:
len(customersplus[customersplus['structure_id'].notna()])

In [ ]:
structure_tag_mappings['structure_id'].nunique()

In [ ]:
def tags_information(tenant_id, first_tags):

    customersplus = load_dataset_2(tenant_id, "customersplus")[['id', 'structure_id']]
    customersplus.rename(columns = {'id' : 'customer_id'}, inplace = True)
    tags = load_dataset_2(tenant_id, "tags")[['id', 'name']]
    tags.rename(columns = {'id' : 'tag_id', 'name' : 'tag_name'}, inplace = True)
    structure_tag_mappings = load_dataset_2(tenant_id, "structure_tag_mappings")[['structure_id', 'tag_id']]
    
    customer_tags = pd.merge(customersplus, structure_tag_mappings, on = 'structure_id', how = 'left')
    customer_tags = pd.merge(customer_tags, tags, on = 'tag_id', how = 'inner')
    
    nb_customers_with_tag = customer_tags['customer_id'].nunique()
    
    print('Nombre de client avec tag : ', nb_customers_with_tag)
    print('Proportion de clients avec tags : ', nb_customers_with_tag/len(customersplus))
    print('Moyenne de tags par client : ', len(customer_tags)/nb_customers_with_tag)
    
    info = customer_tags.groupby(['tag_id', 'tag_name'])['customer_id'].count().reset_index().sort_values('customer_id', ascending = False).head(first_tags)

    return info

In [ ]:
tags_information("1", 20)

In [ ]:
tags_information("2", 20)

In [ ]:
load_dataset_2("2", "tags")[['id', 'name']]

In [ ]:
tags_information("3", 20)

In [ ]:
tags_information("4", 20)

In [ ]:
tags_information("101", 20)

## KPI product

In [ ]:
tenant_id = "1"

df_product = display_databases(tenant_id, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])

df_product.head()

In [ ]:
nb_tickets_per_events = df_product.groupby(['name_event_types', 'name_events'])['ticket_id'].count().reset_index().sort_values('ticket_id', ascending = False)
nb_tickets_per_events['prop_tickets'] = round(nb_tickets_per_events['ticket_id']/len(df_product), 3)
nb_tickets_per_events

# Fin travail 25/02

# Exemple sur Company 1

## Chargement données

In [ ]:
BUCKET = "bdc2324-data/1"
liste_database = fs.ls(BUCKET)

In [ ]:
liste_database_select = ['suppliers', 'ticket', 'purchase', 'consumption', 'type_ofs']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_database_filtered = [element for element in liste_database if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_database_filtered)

In [ ]:
# loop to create dataframes from liste
files_path = liste_database

client_number = files_path[0].split("/")[1]
df_prefix = "df" + str(client_number) + "_"

for i in range(len(files_path)) :
    current_path = files_path[i]
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)
        # the pattern of the name is df1xxx
        nom_dataframe = df_prefix + re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', current_path).group(3)
        globals()[nom_dataframe] = df

## customersplus.csv

In [ ]:
a = pd.DataFrame(df1_customersplus.info())

In [ ]:
def info_colonnes_dataframe(df):
    # Créer une liste pour stocker les informations sur chaque colonne
    infos_colonnes = []

    # Parcourir les colonnes du DataFrame
    for nom_colonne, serie in df.items():  # Utiliser items() au lieu de iteritems()
        # Calculer le taux de valeurs manquantes
        taux_na = serie.isna().mean() * 100

        # Ajouter les informations à la liste
        infos_colonnes.append({
            'Nom_colonne': nom_colonne,
            'Type_colonne': str(serie.dtype),
            'Taux_NA': taux_na
        })

    # Créer une nouvelle DataFrame à partir de la liste d'informations
    df_infos_colonnes = pd.DataFrame(infos_colonnes)

    return df_infos_colonnes

In [ ]:
def cleaning_date(df, column_name):
    """
    Nettoie la colonne spécifiée du DataFrame en convertissant les valeurs en datetime avec le format ISO8601.

    Parameters:
    - df: DataFrame
        Le DataFrame contenant la colonne à nettoyer.
    - column_name: str
        Le nom de la colonne à nettoyer.

    Returns:
    - DataFrame
        Le DataFrame modifié avec la colonne nettoyée.
    """
    df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
    return df

In [ ]:
a = info_colonnes_dataframe(df1_customersplus)

In [ ]:
a

In [ ]:
a = pd.DataFrame(df1_customersplus.isna().sum()/len(df1_customersplus)*100)

In [ ]:
# Selection des variables
df1_customersplus_clean = df1_customersplus.copy()

cleaning_date(df1_customersplus_clean, 'first_buying_date')
cleaning_date(df1_customersplus_clean, 'last_visiting_date')

df1_customersplus_clean.drop(['lastname', 'firstname', 'email', 'civility', 'note', 'created_at', 'updated_at', 'deleted_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode', 'last_visiting_date'], axis = 1, inplace=True)
df1_customersplus_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)



## tickets.csv

In [ ]:
df1_tickets

In [ ]:
df1_tickets.info()

In [ ]:
df1_tickets.isna().sum()/len(df1_tickets)*100

In [ ]:
# Selection des variables
df1_tickets_clean = df1_tickets.drop(['lastname', 'firstname', 'email', 'created_at', 'updated_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode'], axis = 1, inplace=True)
df1_tickets_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)

## suppliers.csv

In [ ]:
df1_suppliers

In [ ]:
df1_suppliers.info()

In [ ]:
df1_suppliers.isna().sum()/len(df1_suppliers)*100

In [ ]:
# Selection des variables
df1_suppliers_clean = df1_suppliers[['id', 'name']]
df1_suppliers_clean.rename(columns = {'name' : 'supplier_name'}, inplace = True)

In [ ]:
df1_suppliers_clean

## type_ofs.csv

In [ ]:
df1_type_ofs

In [ ]:
df1_type_ofs.info()

In [ ]:
# Selection des variables
df1_type_ofs_clean = df1_type_ofs[['id', 'name', 'children']]
df1_type_ofs_clean.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)

## purchases.csv

In [ ]:
df1_purchases

In [ ]:
df1_purchases.info()

In [ ]:
# Nettoyage purchase_date
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], utc = True)
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], format = 'ISO8601')

In [ ]:
df1_purchases.info()

In [ ]:
# Selection des variables
df1_purchases_clean = df1_purchases[['id', 'purchase_date', 'customer_id']]

## Fusion de l'ensemble des données billétiques

In [ ]:
# Fusion avec fournisseurs
df1_ticket_information = pd.merge(df1_tickets_clean, df1_suppliers_clean, left_on = 'supplier_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['supplier_id', 'id'], axis = 1, inplace=True)

# Fusion avec type de tickets
df1_ticket_information = pd.merge(df1_ticket_information, df1_type_ofs_clean, left_on = 'type_of', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['type_of', 'id'], axis = 1, inplace=True)

# Fusion avec achats
df1_ticket_information = pd.merge(df1_ticket_information, df1_purchases_clean, left_on = 'purchase_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['purchase_id', 'id'], axis = 1, inplace=True)

In [ ]:
df1_ticket_information

# Utilisation de fonctions

In [ ]:
# Créer un DataFrame exemple
df_not_clean = df1_campaign_stats[['opened_at']].head(20)

# Appliquer la fonction pour nettoyer la colonne 'purchase_date' de manière vectorisée
df_clean = cleaning_date(df_not_clean, 'opened_at')
df_clean.rename(columns = {'opened_at' : 'opened_at_clean'}, inplace = True)

test = pd.concat([df1_campaign_stats[['opened_at']].head(20), df_clean], axis=1)

test.info()

## Nettoyage, selection et fusion

In [ ]:
df1_ticket_information

In [ ]:
df1_ticket_information.info()

# Customer information

## Target area

In [ ]:
# Target.csv cleaning
df1_targets_clean = df1_targets[["id", "target_type_id", "name"]]
df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)

# target_type cleaning
df1_target_types_clean = df1_target_types[["id","is_import","name"]].add_prefix("target_type_")

#customer_target_mappings cleaning
df1_customer_target_mappings_clean = df1_customer_target_mappings[["id", "customer_id", "target_id"]]

# Merge target et target_type
df1_targets_full = pd.merge(df1_targets_clean, df1_target_types_clean, left_on='target_type_id', right_on='target_type_id', how='inner')
df1_targets_full.drop(['target_type_id'], axis = 1, inplace=True)

# Merge
df1_targets_full = pd.merge(df1_customer_target_mappings_clean, df1_targets_full, left_on='target_id', right_on='target_id', how='inner')
df1_targets_full.drop(['target_id'], axis = 1, inplace=True)

In [ ]:
df1_targets_test = df1_targets_full[['id', 'customer_id']].groupby(['customer_id']).count()
len(df1_targets_test[df1_targets_test['id'] > 1]) / len(df1_targets_test)

# 99,6% des 151 000 client visés sont catégorisés plusieurs fois et en moyenne 5 fois... 
df1_targets_test.mean()


In [ ]:
df1_targets_full.head()

In [ ]:
# Catégorisation des target_name
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist

# Téléchargement des ressources nécessaires
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')



In [ ]:
# Définition des fonctions de tokenisation, suppression des mots vides et lemmatisation
def preprocess_text(texte):
    # Concaténation des éléments de la liste en une seule chaîne de caractères
    texte_concat = ' '.join(texte)
    
    # Tokenisation des mots
    tokens = word_tokenize(texte_concat.lower())
    
    # Suppression des mots vides (stopwords)
    stop_words = set(stopwords.words('french'))
    filtered_tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatisation des mots
    lemmatizer = WordNetLemmatizer()
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]
    
    return lemmatized_tokens


# Appliquer le prétraitement à la colonne de texte
df1_targets_full['target_name_tokened'] = df1_targets_full['target_name'].apply(preprocess_text)

# Concaténer les listes de mots pour obtenir une liste de tous les mots dans le corpus
all_words = [word for tokens in df1_targets_full['target_name_tokened'] for word in tokens]

# Calculer la fréquence des mots
freq_dist = FreqDist(all_words)




In [ ]:
# Affichage des mots les plus fréquents
print("Mots les plus fréquents:")
for mot, freq in freq_dist.most_common(15):
    print(f"{mot}: {freq}")

In [ ]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

# Téléchargement des ressources nécessaires
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

# Création de la DataFrame d'exemple
data = {'texte': ["Le chat noir mange une souris.", "Le chien blanc aboie."]}
df = pd.DataFrame(data)

# Fonction pour prétraiter le texte
def preprocess_text(texte):
    # Concaténation des éléments de la liste en une seule chaîne de caractères
    texte_concat = ' '.join(texte)
    
    # Tokenisation des mots
    tokens = word_tokenize(texte_concat.lower())
    
    # Suppression des mots vides (stopwords)
    stop_words = set(stopwords.words('french'))
    filtered_tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatisation des mots
    lemmatizer = WordNetLemmatizer()
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]
    
    return lemmatized_tokens

# Appliquer la fonction de prétraitement à la colonne de texte
df['texte_preprocessed'] = df['texte'].apply(preprocess_text)

# Afficher le résultat
print(df)


## Campaign area

In [ ]:
# campaign_stats cleaning 
df1_campaign_stats_clean = df1_campaign_stats[["id", "campaign_id", "customer_id", "opened_at", "sent_at", "delivered_at"]]
cleaning_date(df1_campaign_stats_clean, 'opened_at')
cleaning_date(df1_campaign_stats_clean, 'sent_at')
cleaning_date(df1_campaign_stats_clean, 'delivered_at')

# campaigns cleaning
df1_campaigns_clean = df1_campaigns[["id", "name", "service_id", "sent_at"]].add_prefix("campaign_")
cleaning_date(df1_campaigns_clean, 'campaign_sent_at')

# Merge 
df1_campaigns_full = pd.merge(df1_campaign_stats_clean, df1_campaigns_clean, on = "campaign_id", how = "left")
df1_campaigns_full.drop(['campaign_id'], axis = 1, inplace=True)

In [ ]:
df1_campaigns_full.info()

In [ ]:
df1_campaigns_information

## Link area

In [ ]:
df1_campaigns

In [ ]:
df1_link_stats

## Supplier

In [ ]:
# Fonction d'exploration pour suppliers.csv = label itr et commission inconnues
def suppliers_exploration(suppliers = None) : 
    
    # Taux de NaN pour ces colonnes
    label_na = suppliers['label'].isna().sum()/len(suppliers)*100
    itr_na = suppliers['itr'].isna().sum()/len(suppliers)*100
    commission_na = suppliers['commission'].isna().sum()/len(suppliers)*100

    suppliers_desc = pd.DataFrame({'nb_suppliers' : [suppliers['name'].nunique()],
                                  'label_na' : [label_na],
                                  'itr_na' : [itr_na],
                                  'commission_na' : [commission_na]})

    return suppliers_desc

In [ ]:
df1_suppliers_desc = suppliers_exploration(suppliers = df1_suppliers)

In [ ]:
df1_suppliers_desc

In [ ]:
BUCKET = "bdc2324-data"
liste_folders = fs.ls(BUCKET)

liste_files = []
for company_folder in liste_folders : 
    liste_files.extend(fs.ls(company_folder))

In [ ]:
liste_database_select = ['suppliers']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_suppliers = [element for element in liste_files if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_suppliers)

In [ ]:
# loop to create dataframes from file 2
def database_loading(database_name = None):
    files_path = database_name
    
    client_number = files_path.split("/")[1]
    df_prefix = "df" + str(client_number) + "_"
    
    current_path = files_path
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)

    return df, client_number

In [ ]:
df_all = pd.DataFrame()

for link in liste_suppliers:
    
    df_supplier, tenant_id = database_loading(link)
    
    df_supplier['tenant_id'] = int(tenant_id)

    df_all = pd.concat([df_all, df_supplier], axis = 0)
    

In [ ]:
# df_all[df_all['tenant_id'] == 101]['name'].unique()

In [ ]:
liste_mots = ['en ligne', 'internet', 'web', 'net', 'vad', 'online'] 
# vad = vente à distance
df_all['name'] = df_all['name'].fillna('')

df_all['canal_vente_internet'] = df_all['name'].str.contains('|'.join(liste_mots), case=False).astype(int)


In [ ]:
df_all.groupby('tenant_id')['canal_vente_internet'].max()